In [48]:
import pandas as pd
import numpy as np
import xgboost as xgb
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import accuracy_score, recall_score, precision_score, roc_auc_score

In [2]:
data = pd.read_csv('../data/train_clean.csv')

In [3]:
data.head()

respondent_id  h1n1_concern  h1n1_knowledge  behavioral_antiviral_meds  \
0              0           1.0             0.0                        0.0   
1              1           3.0             2.0                        0.0   
2              2           1.0             1.0                        0.0   
3              3           1.0             1.0                        0.0   
4              4           2.0             1.0                        0.0   

   behavioral_avoidance  behavioral_face_mask  behavioral_wash_hands  \
0                   0.0                   0.0                    0.0   
1                   1.0                   0.0                    1.0   
2                   1.0                   0.0                    0.0   
3                   1.0                   0.0                    1.0   
4                   1.0                   0.0                    1.0   

   behavioral_large_gatherings  behavioral_outside_home  \
0                          0.0                      1.0   
1                          0.0                      1.0   
2                          0.0                      0.0   
3                          1.0                      0.0   
4                          1.0                      0.0   

   behavioral_touch_face  ... rent_or_own   employment_status hhs_geo_region  \
0                    1.0  ...         Own  Not in Labor Force       oxchjgsf   
1                    1.0  ...        Rent            Employed       bhuqouqj   
2                    0.0  ...         Own            Employed       qufhixun   
3                    0.0  ...        Rent  Not in Labor Force       lrircsnp   
4                    1.0  ...         Own            Employed       qufhixun   

                 census_msa household_adults household_children  \
0                   Non-MSA              0.0                0.0   
1  MSA, Not Principle  City              0.0                0.0   
2  MSA, Not Principle  City              2.0                0.0   
3       MSA, Principle City              0.0                0.0   
4  MSA, Not Principle  City              1.0                0.0   

   employment_industry  employment_occupation  h1n1_vaccine  seasonal_vaccine  
0          no_response            no_response             0                 0  
1             pxcmvdjn               xgwztkwe             0                 1  
2             rucpziij               xtkaffoo             0                 0  
3          no_response            no_response             0                 1  
4             wxleyezf               emcorrxb             0                 0  

[5 rows x 38 columns]

In [9]:
data.dtypes

respondent_id                    int64
h1n1_concern                   float64
h1n1_knowledge                 float64
behavioral_antiviral_meds      float64
behavioral_avoidance           float64
behavioral_face_mask           float64
behavioral_wash_hands          float64
behavioral_large_gatherings    float64
behavioral_outside_home        float64
behavioral_touch_face          float64
doctor_recc_h1n1                object
doctor_recc_seasonal            object
chronic_med_condition           object
child_under_6_months           float64
health_worker                   object
health_insurance                object
opinion_h1n1_vacc_effective    float64
opinion_h1n1_risk              float64
opinion_h1n1_sick_from_vacc    float64
opinion_seas_vacc_effective    float64
opinion_seas_risk              float64
opinion_seas_sick_from_vacc    float64
age_group                       object
education                       object
race                            object
sex                      

In [14]:
categorical_columns = list(data.select_dtypes('object').columns)
categorical_columns

['doctor_recc_h1n1',
 'doctor_recc_seasonal',
 'chronic_med_condition',
 'health_worker',
 'health_insurance',
 'age_group',
 'education',
 'race',
 'sex',
 'income_poverty',
 'marital_status',
 'rent_or_own',
 'employment_status',
 'hhs_geo_region',
 'census_msa',
 'employment_industry',
 'employment_occupation']

In [15]:
X = data.drop(columns=['h1n1_vaccine', 'seasonal_vaccine'])
y = data['h1n1_vaccine']

In [16]:
Xd = pd.get_dummies(data=X, columns=categorical_columns, drop_first=True)

In [17]:
X_train, X_test, y_train, y_test = train_test_split(Xd, y, random_state=42, stratify=y)

In [23]:
X_train = np.array(X_train)
X_test = np.array(X_test)

In [25]:
y_train = np.array(y_train)
y_test = np.array(y_test)

In [50]:
xg_cls = xgb.XGBClassifier(random_state=42, use_label_encoder=False)

params = {
    'n_estimators' : [100, 200, 250],
    'max_depth' : list(range(3, 11)),
    'learning_rate' : [0.01, 0.005, 0.1, 0.3],
    'colsample_bytree' : [0.5, 0.75, 1],
    'subsample' : [0.6, 0.8, 1] 
}

gs = GridSearchCV(estimator=xg_cls, param_grid=params, scoring='roc_auc')

gs.fit(X_train, y_train)

y_pred = gs.predict(X_test)

C:\ProgramData\Anaconda3\envs\xgboost\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[10:04:54] WARNING: D:\bld\xgboost-split_1645118015404\work\src\learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\ProgramData\Anaconda3\envs\xgboost\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[10:04:54] WARNING: D:\bld\xgboost-split_1645118015404\work\src\learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\ProgramData\Anaconda3\envs\xgboost\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


...

[12:53:21] WARNING: D:\bld\xgboost-split_1645118015404\work\src\learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\ProgramData\Anaconda3\envs\xgboost\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[12:53:33] WARNING: D:\bld\xgboost-split_1645118015404\work\src\learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


C:\ProgramData\Anaconda3\envs\xgboost\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[12:53:38] WARNING: D:\bld\xgboost-split_1645118015404\work\src\learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


In [51]:
gs.best_score_

0.8702111247884003

In [52]:
gs.best_estimator_

XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
              colsample_bynode=1, colsample_bytree=0.5,
              enable_categorical=False, gamma=0, gpu_id=-1,
              importance_type=None, interaction_constraints='',
              learning_rate=0.1, max_delta_step=0, max_depth=3,
              min_child_weight=1, missing=nan, monotone_constraints='()',
              n_estimators=200, n_jobs=16, num_parallel_tree=1,
              predictor='auto', random_state=42, reg_alpha=0, reg_lambda=1,
              scale_pos_weight=1, subsample=1, tree_method='exact',
              validate_parameters=1, verbosity=None)

In [57]:
gs.best_params_

{'colsample_bytree': 0.5,
 'learning_rate': 0.1,
 'max_depth': 3,
 'n_estimators': 200,
 'subsample': 1}

In [53]:
accuracy_score(y_test, y_pred)

0.8487344615845439

In [54]:
precision_score(y_test, y_pred)

0.7114788004136504

In [55]:
recall_score(y_test, y_pred)

0.48484848484848486

In [56]:
roc_auc_score(y_test, y_pred)

0.7158932420438697

#### Scores for predicting h1n1 don't look too good with the current dataset. So I'm going to try a few methods of balancing classes and use the best parameters the grid search found to train a new model

In [59]:
categorical_columns.append('h1n1_vaccine')
categorical_columns.append('seasonal_vaccine')
categorical_columns

['doctor_recc_h1n1',
 'doctor_recc_seasonal',
 'chronic_med_condition',
 'health_worker',
 'health_insurance',
 'age_group',
 'education',
 'race',
 'sex',
 'income_poverty',
 'marital_status',
 'rent_or_own',
 'employment_status',
 'hhs_geo_region',
 'census_msa',
 'employment_industry',
 'employment_occupation',
 'h1n1_vaccine',
 'seasonal_vaccine']

In [76]:

X = data[categorical_columns].drop(columns=['h1n1_vaccine', 'seasonal_vaccine'])
y = data['h1n1_vaccine']

In [83]:
Xd = pd.get_dummies(data=X, columns=list(X.columns), drop_first=True)

In [84]:
X_train, X_test, y_train, y_test = train_test_split(Xd, y, random_state=42, stratify=y)

In [85]:
X_train = np.array(X_train)
X_test = np.array(X_test)

In [86]:
y_train = np.array(y_train)
y_test = np.array(y_test)

In [87]:
model = xgb.XGBClassifier(random_state=42,
                          use_label_encoder=False,
                          colsample_bytree=0.5,
                          learning_rate=0.1,
                          max_depth=3,
                          n_estimators=200,
                          subsample=1
                         )
model.fit(X_train, y_train)


[18:58:22] WARNING: D:\bld\xgboost-split_1645118015404\work\src\learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
              colsample_bynode=1, colsample_bytree=0.5,
              enable_categorical=False, gamma=0, gpu_id=-1,
              importance_type=None, interaction_constraints='',
              learning_rate=0.1, max_delta_step=0, max_depth=3,
              min_child_weight=1, missing=nan, monotone_constraints='()',
              n_estimators=200, n_jobs=16, num_parallel_tree=1,
              predictor='auto', random_state=42, reg_alpha=0, reg_lambda=1,
              scale_pos_weight=1, subsample=1, tree_method='exact',
              use_label_encoder=False, validate_parameters=1, verbosity=None)

In [88]:
test_pred = model.predict(X_test)
train_pred = model.predict(X_train)

In [89]:
accuracy_score(y_test, test_pred), accuracy_score(y_train, train_pred)

(0.8283660326493935, 0.8326510234648028)

In [90]:
precision_score(y_test, test_pred)

0.6447507953340403

In [91]:
recall_score(y_test, test_pred)

0.4284707540521494

In [92]:
roc_auc_score(y_test, test_pred)

0.682379157931362

In [ ]:
doc recommended, opinion 